# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang
***

## Set up and Import Libraries

In [1]:
#install libraries if needed
#!pip3 install pdpipe

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest
from datetime import datetime

In [3]:
#set the root path, change the directory into the project folder
os.chdir("/Users/silvia/cffs-label")

In [4]:
#enable reading data in the scrolling window 
pd.set_option("display.max_rows", None, "display.max_columns", None)

***
## Import Preprocessed Datasets

In [5]:
Preps = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "Preps_Unit_Cleaned.csv"))
Preps.head()

PrepId               Description  PakQty PakUOM InventoryGroup   StdQty  \
0  P-56398           BATCH|Guacamole   2.750     Kg           PREP   2750.0   
1  P-24750          CHOPPED|Cilantro   0.500     Kg            NaN    500.0   
2  P-41574        COOKED|Black Beans  30.000     Kg           PREP  30000.0   
3  P-26068  COOKED|Caramelized Onion   1.200     Kg           PREP   1200.0   
4  P-28258          COOKED|Chow Mein  48.081     Kg           PREP  48081.0   

  StdUom  
0      g  
1      g  
2      g  
3      g  
4      g

In [6]:
ghge_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "ghge_factors.csv"))
ghge_factors.head()

Category ID              Food Category  \
0            1        beef & buffalo meat   
1            2    lamb/mutton & goat meat   
2            3            pork (pig meat)   
3            4  poultry (chicken, turkey)   
4            5                     butter   

   Active Total Supply Chain Emissions (kg CO2 / kg food)  
0                                            41.3463       
1                                            41.6211       
2                                             9.8315       
3                                             4.3996       
4                                            11.4316

In [7]:
nitro_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "nitrogen_factors.csv"))
nitro_factors.head()

Category ID              Food Category  g N lost/kg product
0            1        beef & buffalo meat               329.50
1            2    lamb/mutton & goat meat               231.15
2            3            pork (pig meat)               132.80
3            4  poultry (chicken, turkey)               116.80
4            5                     butter               100.35

In [8]:
water_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "water_factors.csv"))
water_factors.head()

Category ID              Food Category  Freshwater Withdrawals (L/FU)  \
0            1        beef & buffalo meat                       1677.200   
1            2    lamb/mutton & goat meat                        461.200   
2            3            pork (pig meat)                       1810.300   
3            4  poultry (chicken, turkey)                        370.300   
4            5                     butter                       1010.176   

   Stress-Weighted Water Use (L/FU)  
0                         61309.000  
1                           258.900  
2                         54242.700  
3                           333.500  
4                         50055.168

In [9]:
# Load current Items List with assigned Emission Factors Category ID
Items_Assigned = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv"))
Items_Assigned.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545           1   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869           1       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064           1     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005           1            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002           1  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

***
## Import Update Info

In [10]:
#import list of prep that need convert uom to standard uom manually
Manual_PrepU = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "update", "Preps_UpdateUom.csv"))
Manual_PrepU.head()

PrepId                 Description  PakQty PakUOM InventoryGroup   StdQty  \
0  P-54697             LEMON|Wedge 1/8     8.0   each           PREP     84.0   
1  P-35132  MARINATED|Lemon & Herb Chx   185.0     ea           PREP  24050.0   
2  P-51992   YIELD|Bread|Sourdough 5/8    36.0  slice            NaN   1620.0   
3  P-26234  BATCH|Roasted Garlic Bread    16.0     ea           PREP   1280.0   
4  P-26170           GRILLED|NaanBread     1.0     ea           PREP    125.0   

  StdUom  
0      g  
1      g  
2      g  
3      g  
4      g

In [11]:
#select the file path for new items list with category id
New_Items_Added = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "new items added", "New_Items_Added_7.csv"))
New_Items_Added

ItemId  CategoryID                     Description  CaseQty CaseUOM  \
0   I-13422          59        BURGER 4OZ NATURAL HALAL        1      cs   
1   I-63034          59  BURGER VEG MALIBU GARDENBURGER       48      CT   
2   I-64468           4  CHICK BREAST CRUNCH BREADED FZ        4      Kg   
3    I-1254          24      CIABATTA BUN 5"X 5" PLAIN        12      CT   
4   I-62225          11          EGG LRG 15 DOZEN LOOSE       15     DOZ   
5   I-62736          24    HAMBURGER BUN WW VEGAN 100gr        1      ea   
6   I-64492          24               LOAF GARLIC BREAD        1    LOAF   
7    I-3356           9            MILK CONDENSED SWEET       24  SM CAN   
8    I-1223          24         PANINI SUB ITALIAN - 7"       12      CT   
9   I-53707          54                    PAPRIKA BULK        5      lb   
10   I-5115          12    SAL SOX FLT S/ON PBO PRV  OW        1      lb   
11  I-29357          55            Soup 1 (10L mon-fri)       10       L   
12  I-29356          55            Soup 2 (10L mon-fri)       10       L   
13   I-1273          24        SOURDOUGH BREAD COUNTRY         1    LOAF   
14  I-63866          37              TOMATO POLPA MUTTI       10      Kg   
15   I-2281          10    YOGURT VANILLA STIRRED 650G         1     TUB   

    PakQty PakUOM   InventoryGroup  
0       42     CT             MEAT  
1        1     CT   FOOD - GROCERY  
2        1     Kg          POULTRY  
3        1     CT            BREAD  
4       12     CT            DAIRY  
5        1     ea            BREAD  
6        1   LOAF            BREAD  
7      300     ml   FOOD - GROCERY  
8        1     CT            BREAD  
9        1     lb           SPICES  
10       1     lb          SEAFOOD  
11       1      L  PRODUCTION FOOD  
12       1      L  PRODUCTION FOOD  
13       1   LOAF            BREAD  
14       1     Kg   FOOD - GROCERY  
15       1   650G            DAIRY

In [12]:
#import list of items that adjusted GHGe factor manually
Manual_Factor = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Manual_Adjust_Factors.csv"))
Manual_Factor.head()

ItemId  CategoryID                   Description  CaseQty CaseUOM  PakQty  \
0  I-52090          59  BURGER BEEF & MUSHROOM HALAL      1.0      cs   48.00   
1  I-45558          59           Prep-Vegan Parmesan   1000.0       g    1.00   
2   I-3352          59        MAYONNAISE PAIL TFC 4L      2.0    each    4.00   
3   I-3223          59  COCONUT MILK 17/19% MILK FAT      6.0  LG CAN    2.84   
4   I-2898          59      MUSTARD DIJON WINE FLEUR      6.0     jar    1.00   

  PakUOM   InventoryGroup  \
0     CT             MEAT   
1      g  PRODUCTION FOOD   
2      L   FOOD - GROCERY   
3      L   FOOD - GROCERY   
4     Kg   FOOD - GROCERY   

   Active Total Supply Chain Emissions (kg CO2 / kg food)  \
0                                           25.00894        
1                                            3.85686        
2                                            3.55000        
3                                            3.50000        
4                                            3.32600        

   g N lost/kg product  Freshwater Withdrawals (L/FU)  \
0               200.86                        1038.84   
1                 0.00                           0.00   
2                 0.00                           0.00   
3                 0.00                           1.00   
4                 0.00                           0.00   

   Stress-Weighted Water Use (L/FU)  
0                           37961.2  
1                               0.0  
2                               0.0  
3                               1.0  
4                               0.0

### Update Correct Uom for Preps

In [13]:
#update prep list with manully adjusted uom
for index, row in Manual_PrepU.iterrows():
    PrepId = Manual_PrepU.loc[index, 'PrepId']
    qty = Manual_PrepU.loc[index, 'StdQty']
    uom = Manual_PrepU.loc[index, 'StdUom']
    Preps.loc[Preps['PrepId'] == PrepId, 'StdQty'] = qty
    Preps.loc[Preps['PrepId'] == PrepId, 'StdUom'] = uom

In [14]:
Preps.drop_duplicates(subset=['PrepId'], inplace=True,)

In [15]:
Preps.head()

PrepId               Description  PakQty PakUOM InventoryGroup   StdQty  \
0  P-56398           BATCH|Guacamole   2.750     Kg           PREP   2750.0   
1  P-24750          CHOPPED|Cilantro   0.500     Kg            NaN    500.0   
2  P-41574        COOKED|Black Beans  30.000     Kg           PREP  30000.0   
3  P-26068  COOKED|Caramelized Onion   1.200     Kg           PREP   1200.0   
4  P-28258          COOKED|Chow Mein  48.081     Kg           PREP  48081.0   

  StdUom  
0      g  
1      g  
2      g  
3      g  
4      g

In [16]:
Preps.shape

(493, 7)

In [17]:
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_List_Cleaned.csv")
Preps.to_csv(path, index = False, header = True)

### Import List of New Items with Emission Factors Category ID Assigned

In [18]:
frames = [Items_Assigned, New_Items_Added]
Items_Assigned_Updated = pd.concat(frames).reset_index(drop=True, inplace=False).drop_duplicates()
Items_Assigned_Updated.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545           1   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869           1       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064           1     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005           1            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002           1  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [19]:
Items_Assigned_Updated.shape

(1937, 8)

In [20]:
Items_Assigned_Updated[['CategoryID']] = Items_Assigned_Updated[['CategoryID']].apply(pd.to_numeric)

In [21]:
path = os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv")
Items_Assigned_Updated.to_csv(path, index = False, header = True)

## Mapping Items to Footprint Factors

In [22]:
# map GHG footprint factors
mapping = pd.merge(Items_Assigned_Updated, ghge_factors.loc[:,['Category ID','Food Category','Active Total Supply Chain Emissions (kg CO2 / kg food)']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')
for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'Active Total Supply Chain Emissions (kg CO2 / kg food)'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-10775           1       HOT DOG BEEF 8IN 4/LB FZN     10.000       lb   
14    I-17671           1    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000       Kg   
15    I-20879           1       SOUVLAKI BEEF 75G SKEWERS      1.000       CT   
16     I-3842           1          BEEF INSIDE ROUND AAA       1.000       Kg   
17     I-3846           1        BEEF LEAN GRD COMMERCIAL      5.000       Kg   
18     I-3867           1        BEEF STIRFRY MEAT FZ 1ST      5.000       Kg   
19     I-9454           1         BEEF BACK RIB UT COV FZ      1.000       Kg   
20    I-26667           1          BURGER PRIME RIB  6OZ      30.000       ea   
21    I-28697           1               BURGER QUINOA YAM     60.000       ea   
22    I-47440           1             JAMAICAN PATTY MILD     36.000       ea   
23    I-47441           1            JAMAICAN PATTY SPICY     36.000       ea   
24    I-13425           2    LAMB LEG BNLS COMMODITY AUST      1.000       Kg   
25     I-3843           2                      LAMB GRDFR      1.000       Kg   
26    I-43653           2                  LAMB STEW 3/4"     25.000       Kg   
27    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
28    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
29    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
30     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
31    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
32     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
33     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
34     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
35     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
36     I-3855           3                   PORK GRD FRZ       5.000       Kg   
37     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
38     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
39     I-2310           3                      HAM HONEY       6.000      pak   
40     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
41     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
42    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
43     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
44     I-2305           3                  BACON PANCETTA      1.000       Kg   
45    I-13423           3                   PORK STIR FRY      5.000       Kg   
46    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
47     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
48    I-42350           3       PORK B

In [23]:
# map nitrogen footprint factors
mapping = pd.merge(mapping, nitro_factors.loc[:,['Category ID','Food Category','g N lost/kg product']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')

for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'g N lost/kg product'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-10775           1       HOT DOG BEEF 8IN 4/LB FZN     10.000       lb   
14    I-17671           1    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000       Kg   
15    I-20879           1       SOUVLAKI BEEF 75G SKEWERS      1.000       CT   
16     I-3842           1          BEEF INSIDE ROUND AAA       1.000       Kg   
17     I-3846           1        BEEF LEAN GRD COMMERCIAL      5.000       Kg   
18     I-3867           1        BEEF STIRFRY MEAT FZ 1ST      5.000       Kg   
19     I-9454           1         BEEF BACK RIB UT COV FZ      1.000       Kg   
20    I-26667           1          BURGER PRIME RIB  6OZ      30.000       ea   
21    I-28697           1               BURGER QUINOA YAM     60.000       ea   
22    I-47440           1             JAMAICAN PATTY MILD     36.000       ea   
23    I-47441           1            JAMAICAN PATTY SPICY     36.000       ea   
24    I-13425           2    LAMB LEG BNLS COMMODITY AUST      1.000       Kg   
25     I-3843           2                      LAMB GRDFR      1.000       Kg   
26    I-43653           2                  LAMB STEW 3/4"     25.000       Kg   
27    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
28    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
29    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
30     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
31    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
32     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
33     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
34     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
35     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
36     I-3855           3                   PORK GRD FRZ       5.000       Kg   
37     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
38     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
39     I-2310           3                      HAM HONEY       6.000      pak   
40     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
41     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
42    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
43     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
44     I-2305           3                  BACON PANCETTA      1.000       Kg   
45    I-13423           3                   PORK STIR FRY      5.000       Kg   
46    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
47     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
48    I-42350           3       PORK B

In [24]:
# map water footprint factors
mapping = pd.merge(mapping, water_factors.loc[:,['Category ID','Food Category','Freshwater Withdrawals (L/FU)', 'Stress-Weighted Water Use (L/FU)']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')

for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'Freshwater Withdrawals (L/FU)'] = 0
        mapping.loc[index,'Stress-Weighted Water Use (L/FU)'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-10775           1       HOT DOG BEEF 8IN 4/LB FZN     10.000       lb   
14    I-17671           1    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000       Kg   
15    I-20879           1       SOUVLAKI BEEF 75G SKEWERS      1.000       CT   
16     I-3842           1          BEEF INSIDE ROUND AAA       1.000       Kg   
17     I-3846           1        BEEF LEAN GRD COMMERCIAL      5.000       Kg   
18     I-3867           1        BEEF STIRFRY MEAT FZ 1ST      5.000       Kg   
19     I-9454           1         BEEF BACK RIB UT COV FZ      1.000       Kg   
20    I-26667           1          BURGER PRIME RIB  6OZ      30.000       ea   
21    I-28697           1               BURGER QUINOA YAM     60.000       ea   
22    I-47440           1             JAMAICAN PATTY MILD     36.000       ea   
23    I-47441           1            JAMAICAN PATTY SPICY     36.000       ea   
24    I-13425           2    LAMB LEG BNLS COMMODITY AUST      1.000       Kg   
25     I-3843           2                      LAMB GRDFR      1.000       Kg   
26    I-43653           2                  LAMB STEW 3/4"     25.000       Kg   
27    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
28    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
29    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
30     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
31    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
32     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
33     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
34     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
35     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
36     I-3855           3                   PORK GRD FRZ       5.000       Kg   
37     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
38     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
39     I-2310           3                      HAM HONEY       6.000      pak   
40     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
41     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
42    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
43     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
44     I-2305           3                  BACON PANCETTA      1.000       Kg   
45    I-13423           3                   PORK STIR FRY      5.000       Kg   
46    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
47     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
48    I-42350           3       PORK B

### Manully Adjust Footprint Factor for Specific Items

In [25]:
for index, row in Manual_Factor.iterrows():
    itemId = Manual_Factor.loc[index, 'ItemId']
    ghge = Manual_Factor.loc[index, 'Active Total Supply Chain Emissions (kg CO2 / kg food)']
    nitro = Manual_Factor.loc[index, 'g N lost/kg product']
    water = Manual_Factor.loc[index, 'Freshwater Withdrawals (L/FU)']
    str_water = Manual_Factor.loc[index, 'Stress-Weighted Water Use (L/FU)']
    mapping.loc[mapping['ItemId'] == itemId, 'Active Total Supply Chain Emissions (kg CO2 / kg food)'] = ghge
    mapping.loc[mapping['ItemId'] == itemId, 'g N lost/kg product'] = nitro
    mapping.loc[mapping['ItemId'] == itemId, 'Freshwater Withdrawals (L/FU)'] = water
    mapping.loc[mapping['ItemId'] == itemId, 'Stress-Weighted Water Use (L/FU)'] = str_water

In [26]:
mapping.drop_duplicates(subset = ['ItemId'], inplace=True)
mapping.dtypes

ItemId                                                     object
CategoryID                                                  int64
Description                                                object
CaseQty                                                   float64
CaseUOM                                                    object
PakQty                                                    float64
PakUOM                                                     object
InventoryGroup                                             object
Active Total Supply Chain Emissions (kg CO2 / kg food)    float64
g N lost/kg product                                       float64
Freshwater Withdrawals (L/FU)                             float64
Stress-Weighted Water Use (L/FU)                          float64
dtype: object

In [27]:
mapping.shape

(1937, 12)

In [28]:
mapping

ItemId  CategoryID                     Description    CaseQty  CaseUOM  \
0     I-57545           1         CHUCK FLAT BONELESS FZN      3.300       Kg   
1     I-10869           1             BEEF STIRFRY COV FR      5.000       Kg   
2      I-7064           1           BEEF OUTSIDE FLAT AAA      1.000       Kg   
3     I-37005           1                  BEEF MEATBALLS      4.540       Kg   
4     I-37002           1        BEEF INSIDE ROUND SHAVED      9.000       Kg   
5      I-3876           1           BEEF CHUCK GROUND AAA      1.000       Kg   
6     I-34065           1           BEEF BONES KNUCKLE FZ      1.000       Kg   
7     I-11661           1           BEEF STEW 3/4" FROZEN      5.000       Kg   
8      I-3837           1          BEEF STEW DICED 3/4"FR      1.000       Kg   
9     I-43648           1       BRISKET BEEF CORN SMKD FR      4.500       Kg   
10     I-3838           1      BEEF BRISKET BNLS 3/4" AAA      1.000       Kg   
11    I-49128           1       HOT DOG BEEF G/FREE 6 INC     10.000       lb   
12    I-17055           1   BEEF RIB BRAISING 3 BONE 1/4"      1.000       Kg   
13    I-10775           1       HOT DOG BEEF 8IN 4/LB FZN     10.000       lb   
14    I-17671           1    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000       Kg   
15    I-20879           1       SOUVLAKI BEEF 75G SKEWERS      1.000       CT   
16     I-3842           1          BEEF INSIDE ROUND AAA       1.000       Kg   
17     I-3846           1        BEEF LEAN GRD COMMERCIAL      5.000       Kg   
18     I-3867           1        BEEF STIRFRY MEAT FZ 1ST      5.000       Kg   
19     I-9454           1         BEEF BACK RIB UT COV FZ      1.000       Kg   
20    I-26667           1          BURGER PRIME RIB  6OZ      30.000       ea   
21    I-28697           1               BURGER QUINOA YAM     60.000       ea   
22    I-47440           1             JAMAICAN PATTY MILD     36.000       ea   
23    I-47441           1            JAMAICAN PATTY SPICY     36.000       ea   
24    I-13425           2    LAMB LEG BNLS COMMODITY AUST      1.000       Kg   
25     I-3843           2                      LAMB GRDFR      1.000       Kg   
26    I-43653           2                  LAMB STEW 3/4"     25.000       Kg   
27    I-13303           3            SAUSAGE PATTIES PORK      5.000       Kg   
28    I-11922           3       SAUSAGE MEAT CHORIZO FRZN      5.000       CT   
29    I-50575           3    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000      bag   
30     I-2317           3    SAUSAGE FARMER DOUBLE SMOKED      1.000       Kg   
31    I-17667           3            SAUSAGE CHORIZO MEAT      5.000       Kg   
32     I-2333           3   PROSCIUTTO SLICED SAN DANIELE      1.000       Kg   
33     I-6869           3  PROSCIUTTO COTTO MASTRO SLICED      1.000       Kg   
34     I-3856           3      PORK LOIN BNLS S/CUT COVFR      1.000       Kg   
35     I-3887           3       PORK GROUND BRITCO PER KG      1.000       Kg   
36     I-3855           3                   PORK GRD FRZ       5.000       Kg   
37     I-3851           3       PORK BUTT BNLS 1/4 COV FR      1.000       Kg   
38     I-2311           3            HAM PROSCIUTTO BNLS       1.000       Kg   
39     I-2310           3                      HAM HONEY       6.000      pak   
40     I-2306           3            HAM BLACK FOREST slc      6.000      pak   
41     I-8260           3       CAPICOLLO EXT HOT CAPOLLA      1.000       Kg   
42    I-27410           3        BACON 3MM NATURALLY SMKD      5.000       Kg   
43     I-2308           3                 HAM CAPICOLLIFR      1.000       Kg   
44     I-2305           3                  BACON PANCETTA      1.000       Kg   
45    I-13423           3                   PORK STIR FRY      5.000       Kg   
46    I-19657           3               SAUSAGE ANDOUILLE      5.000       Kg   
47     I-2319           3         SMOKIES 5.5 CT BAVARIAN      1.000       Kg   
48    I-42350           3       PORK B

In [29]:
path = os.path.join(os.getcwd(), "data", "mapping", "Mapping.csv")
mapping.to_csv(path, index = False, header = True)